<a href="https://colab.research.google.com/github/marinathomas/SentimentAnalysisHN/blob/master/HN_SentimentAnalysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.cloud import bigquery
import pandas as pd
import os

from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
credential_path = "/content/gdrive/Shared drives/HackerNews:SentimentAnalysis/BigData-HackerNews-77d9fa1b02c1.json"
os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = credential_path

1. Load the BigQuery client
2. Get a reference to HackerNews dataset
3. Load the data set

In [0]:
client = bigquery.Client()
hn_dataset_ref = client.dataset('hacker_news', project='bigquery-public-data')
hn_dset = client.get_dataset(hn_dataset_ref)

In [4]:
query = """
SELECT *
FROM `bigquery-public-data.hacker_news.full`
where  REGEXP_CONTAINS(title, r"(S|s)how HN") 
and (deleted IS NULL or deleted IS FALSE) and  EXTRACT(YEAR FROM timestamp)=2017
ORDER BY SCORE desc
LIMIT 10
"""

query_job = client.query(query)
iterator = query_job.result(timeout=30)
rows = list(iterator)

# Transform the rows into a nice pandas dataframe
max_descendants = pd.DataFrame(data=[list(x.values()) for x in rows], columns=list(rows[0].keys()))
max_descendants.head(10)

title  ... deleted
0  Show HN: Airmash – Multiplayer Missile Warfare...  ...    None
1           Show HN: Sorting Two Metric Tons of Lego  ...    None
2  Show HN: Privacy-focused, ad-free, non-trackin...  ...    None
3  Show HN: Alacritty, a GPU-accelerated terminal...  ...    None
4  Show HN: Get Paid to Build Your Next Side Project  ...    None
5  Show HN: Monica, an open-source CRM to manage ...  ...    None
6          Show HN: A stop-motion video of an engine  ...    None
7       Show HN: Is the stock market going to crash?  ...    None
8  Show HN: A guide to all HTML5 elements and att...  ...    None
9  Show HN: Arxiv Vanity – Read academic papers f...  ...    None

[10 rows x 14 columns]

In [56]:
query = """
select  *
from `bigquery-public-data.hacker_news.full` 
where type = 'comment'  and (deleted IS NULL or deleted IS FALSE) and
parent in (select id from `bigquery-public-data.hacker_news.full` where REGEXP_CONTAINS(title, r"(S|s)how HN") and  EXTRACT(YEAR FROM timestamp)=2017 and (deleted IS NULL or deleted IS FALSE) ORDER BY SCORE desc LIMIT 5)
order by parent ;
"""
query_job = client.query(query)
iterator = query_job.result(timeout=30)
rows = list(iterator)

# Transform the rows into a nice pandas dataframe
comments = pd.DataFrame(data=[list(x.values()) for x in rows], columns=list(rows[0].keys()))
comments.head(20)

TimeoutError: ignored

In [6]:
!pip install vaderSentiment

     |████████████████████████████████| 133kB 2.8MB/s 


In [0]:
from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
analyser = SentimentIntensityAnalyzer()

In [52]:
for index,row in comments.iterrows():
    sentence = row['text']
    score = analyser.polarity_scores(str(sentence))
    print("{:-<40} {}".format(sentence, str(score)))


<a href="https:&#x2F;&#x2F;www.youtube.com&#x2F;watch?v=orPiPpaeN3E" rel="nofollow">https:&#x2F;&#x2F;www.youtube.com&#x2F;watch?v=orPiPpaeN3E</a> {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
Good idea. I will add the feature soon in upcoming versions. Thanks for the feedback. {'neg': 0.0, 'neu': 0.674, 'pos': 0.326, 'compound': 0.7003}
Doesn&#x27;t SoundCloud offer this already? {'neg': 0.0, 'neu': 1.0, 'pos': 0.0, 'compound': 0.0}
Looks like a nice micro quad. Have you considered sending out some examples for reviewers (Flitetest on YT as an example) ?<p>It might be worth it marketing wise. {'neg': 0.0, 'neu': 0.691, 'pos': 0.309, 'compound': 0.8519}
This is cool and I&#x27;m tempted.  However I was disappointed to see that Quads these days are still using the ESC abstraction;
ISTM that there would be much benefit and savings from a tighter integration, or at least a better digital and bidirectional ESC protocol (yes, I did checkout OneShot and MultiShot - not it). {'neg': 0

TypeError: ignored

In [4]:
query = """
select  *
from `bigquery-public-data.hacker_news.full` 
where type = 'comment' and  
parent in (select id from `bigquery-public-data.hacker_news.full` where REGEXP_CONTAINS(title, r"(S|s)how HN") and descendants > 550)
order by parent, timestamp asc;


"""

query_job = client.query(query)
iterator = query_job.result(timeout=30)
rows = list(iterator)

# Transform the rows into a nice pandas dataframe
max_desc_comments = pd.DataFrame(data=[list(x.values()) for x in rows], columns=list(rows[0].keys()))
max_desc_comments.fillna(0, inplace=True)
max_desc_comments.head()

title  url  ... ranking deleted
0      0    0  ...       0       0
1      0    0  ...       0       0
2      0    0  ...       0       0
3      0    0  ...       0       0
4      0    0  ...       0       0

[5 rows x 14 columns]

In [0]:
!pip install TextBlob

In [0]:
from textblob import TextBlob
for index,row in max_desc_comments.iterrows():
    sentence = row['text']
    testimonial = TextBlob(str(sentence))
    print("{:-<40} {}".format(sentence, testimonial.sentiment))

Looks neat. As an aside, why is it named after a woman? I&#x27;m genuinely curious. Sentiment(polarity=-0.1, subjectivity=1.0)
Founder here. Here to answer any questions you might have. The site is not perfect, it&#x27;s not mobile optimized, there are probably bugs, there is a gazillion features missing, no APIs but it&#x27;s a labour of love, open-source and I hope it will help people other than me. I want to grow this product but I need to know what you need, people.
Edit: sorry for the bugs I see on my server popping here and there. Didnt expect that much users and traffic. Sentiment(polarity=-0.10416666666666667, subjectivity=0.5375)
I like it! I definitely could use something like this. I am GLAD that you mention &quot;It’s for your eyes only.&quot;. Very important feature. Sentiment(polarity=0.34, subjectivity=0.8333333333333334)
Thanks for making this open-source. It seems to use Homestead for deployments and Homestead apparently needs a VM. Is there a way to make this work wit

In [9]:
for index,row in max_desc_comments.iterrows():
    sentence = row['text']
    print("----------------------------------------")
    print(sentence)

----------------------------------------
Looks neat. As an aside, why is it named after a woman? I&#x27;m genuinely curious.
----------------------------------------
Founder here. Here to answer any questions you might have. The site is not perfect, it&#x27;s not mobile optimized, there are probably bugs, there is a gazillion features missing, no APIs but it&#x27;s a labour of love, open-source and I hope it will help people other than me. I want to grow this product but I need to know what you need, people.
Edit: sorry for the bugs I see on my server popping here and there. Didnt expect that much users and traffic.
----------------------------------------
I like it! I definitely could use something like this. I am GLAD that you mention &quot;It’s for your eyes only.&quot;. Very important feature.
----------------------------------------
Thanks for making this open-source. It seems to use Homestead for deployments and Homestead apparently needs a VM. Is there a way to make this work wi

In [21]:
query = """
SELECT *
FROM `bigquery-public-data.hacker_news.comments`  order by parent desc
LIMIT 20
"""

query_job = client.query(query)
iterator = query_job.result(timeout=30)
rows = list(iterator)

comments = pd.DataFrame(data=[list(x.values()) for x in rows], columns=list(rows[0].keys()))
comments.fillna(0, inplace=True)
comments.head(20)

id             by         author  ...  deleted  dead ranking
0   10379195       rhaps0dy       rhaps0dy  ...        0     0       0
1   10379182         moomin         moomin  ...        0     0       1
2   10379137      vbezhenar      vbezhenar  ...        0     0       0
3   10379126       sitharus       sitharus  ...        0     0       2
4   10379131           spuz           spuz  ...        0     0       1
5   10379142           dagw           dagw  ...        0     0       0
6   10379132           x5n1           x5n1  ...        0     0       0
7   10379179          mc808          mc808  ...        0     0       0
8   10379149    deathanatos    deathanatos  ...        0     0       1
9   10379163    jcrawfordor    jcrawfordor  ...        0     0       0
10  10379144         SilasX         SilasX  ...        0     0       0
11  10379102        mikeash        mikeash  ...        0     0       0
12  10379184       spike021       spike021  ...        0     0       0
13  10379150  david_servais  david_servais  ...        0     0       1
14  10379152  david_servais  david_servais  ...        0  True       2
15  10379151  david_servais  david_servais  ...        0     0       0
16  10379068         yuhong         yuhong  ...        0     0       0
17  10379183     wingerlang     wingerlang  ...        0     0       0
18  10379079    JonnieCache    JonnieCache  ...        0     0       0
19  10379122           corv           corv  ...        0     0       0

[20 rows x 10 columns]